# Title: Exam 1 -Take-home Portion
# Author: Matthias Quinn
# Date Began: 17th October, 2021
# Data Set Used: [Adults](https://archive-beta.ics.uci.edu/ml/datasets/adult)
# Sources:
# Notes:

## Importing the necessary libraries:

In [1]:
import re
import matplotlib.pyplot as plt
import plotly.express as px
import seaborn as sns
import pandas as pd
import numpy as np
import os
pd.set_option('display.max_columns', 10)
pd.set_option('display.max_rows', 200)

## Importing the Census dataset:

In [2]:
columns = ['Age', 'WorkClass', 'FnlWGT', 'Education',
         'Education_Num', 'Marital', 'Occupation',
         'Relationship', "Race", "Sex", "Capital_Gain",
         "Capital_Loss", "Hours_Week", "NativeCountry",
         "Income"]

trainAdults = pd.read_excel("Adults.xlsx", sheet_name="Train", header=None, names=columns,
                            na_values="?")
testAdults = pd.read_excel("Adults.xlsx", sheet_name="Test", header=None, names=columns,
                           na_values="?")
trainAdults.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32561 entries, 0 to 32560
Data columns (total 15 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   Age            32561 non-null  int64 
 1   WorkClass      32561 non-null  object
 2   FnlWGT         32561 non-null  int64 
 3   Education      32561 non-null  object
 4   Education_Num  32561 non-null  int64 
 5   Marital        32561 non-null  object
 6   Occupation     32561 non-null  object
 7   Relationship   32561 non-null  object
 8   Race           32561 non-null  object
 9   Sex            32561 non-null  object
 10  Capital_Gain   32561 non-null  int64 
 11  Capital_Loss   32561 non-null  int64 
 12  Hours_Week     32561 non-null  int64 
 13  NativeCountry  32561 non-null  object
 14  Income         32561 non-null  object
dtypes: int64(6), object(9)
memory usage: 3.7+ MB


In [3]:
testAdults.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16281 entries, 0 to 16280
Data columns (total 15 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   Age            16281 non-null  int64 
 1   WorkClass      16281 non-null  object
 2   FnlWGT         16281 non-null  int64 
 3   Education      16281 non-null  object
 4   Education_Num  16281 non-null  int64 
 5   Marital        16281 non-null  object
 6   Occupation     16281 non-null  object
 7   Relationship   16281 non-null  object
 8   Race           16281 non-null  object
 9   Sex            16281 non-null  object
 10  Capital_Gain   16281 non-null  int64 
 11  Capital_Loss   16281 non-null  int64 
 12  Hours_Week     16281 non-null  int64 
 13  NativeCountry  16281 non-null  object
 14  Income         16281 non-null  object
dtypes: int64(6), object(9)
memory usage: 1.9+ MB


## Combine the train and test sets for $1$ unified Adults dataset:

Should have 48,842 instances and 15 columns, including the response variable.

In [4]:
Adults = pd.concat([trainAdults, testAdults])
Adults.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 48842 entries, 0 to 16280
Data columns (total 15 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   Age            48842 non-null  int64 
 1   WorkClass      48842 non-null  object
 2   FnlWGT         48842 non-null  int64 
 3   Education      48842 non-null  object
 4   Education_Num  48842 non-null  int64 
 5   Marital        48842 non-null  object
 6   Occupation     48842 non-null  object
 7   Relationship   48842 non-null  object
 8   Race           48842 non-null  object
 9   Sex            48842 non-null  object
 10  Capital_Gain   48842 non-null  int64 
 11  Capital_Loss   48842 non-null  int64 
 12  Hours_Week     48842 non-null  int64 
 13  NativeCountry  48842 non-null  object
 14  Income         48842 non-null  object
dtypes: int64(6), object(9)
memory usage: 6.0+ MB


# Exploratory Data Analsis:

This section will be used to explore the data and to identify any potential issues.

First, create a list of the continuous and categorical variables.

Starting out, there should be **6** continuous features and **8** categorical features.

In [5]:
"Variable Classes"
Continuous = list(Adults.select_dtypes(include=['int64', 'float64']).columns)
Categorical = list(Adults.select_dtypes(include=['object', 'category']).columns)
Categorical.remove("Income")  # Replace Class with your response variable

print(f"Categorical Variables:\n{Categorical}")  # Check to make sure your response is not in this list
print("")
print(f"Continous Variables:\n{Continuous}")

Categorical Variables:
['WorkClass', 'Education', 'Marital', 'Occupation', 'Relationship', 'Race', 'Sex', 'NativeCountry']

Continous Variables:
['Age', 'FnlWGT', 'Education_Num', 'Capital_Gain', 'Capital_Loss', 'Hours_Week']


Let's take a closer look at the categorical variables:

In [6]:
"Tabulation Data:"
for name in Categorical:
    print(name, ":")
    print(Adults[name].value_counts(), "\n")

WorkClass :
 Private             33906
 Self-emp-not-inc     3862
 Local-gov            3136
 ?                    2799
 State-gov            1981
 Self-emp-inc         1695
 Federal-gov          1432
 Without-pay            21
 Never-worked           10
Name: WorkClass, dtype: int64 

Education :
 HS-grad         15784
 Some-college    10878
 Bachelors        8025
 Masters          2657
 Assoc-voc        2061
 11th             1812
 Assoc-acdm       1601
 10th             1389
 7th-8th           955
 Prof-school       834
 9th               756
 12th              657
 Doctorate         594
 5th-6th           509
 1st-4th           247
 Preschool          83
Name: Education, dtype: int64 

Marital :
 Married-civ-spouse       22379
 Never-married            16117
 Divorced                  6633
 Separated                 1530
 Widowed                   1518
 Married-spouse-absent      628
 Married-AF-spouse           37
Name: Marital, dtype: int64 

Occupation :
 Prof-specialty       61

Based on the output of the various frequency tables from above, it looks like we're going to have to combine some levels to make them more meaningful.

For example, taking a look at the top $5$ most common occupation values, we see that the top $5$ occupations are:

    1. Private
   
    2. Self-emp-not-inc
   
    3. Local-gov

    4. ?

    5. Stage-gov

Also, it would make sense to drop the **'?'** value, since it's not a real occupation.

## Taking a closer look at the response variable:

The response variable is the **'Income'** column, so it's important to get a sense of the distribution of this variable.

In [7]:
IncomeDist = Adults["Income"].value_counts()
fig = px.bar(IncomeDist, x=IncomeDist.index, y=IncomeDist.values, color=IncomeDist.index, title="Distribution of Response Variable")
fig.update_yaxes(title="Count")
fig.update_xaxes(title="Income Category")
fig.show()

It is evident that the response variable is not in a proper **binary** format. Let's fix that next:

In [8]:
"To refactor the levels of a variable in a dataset:"

Adults["Income"].value_counts()

Adults["Income"] = Adults["Income"].map({" <=50K": "Less50K",
                                 " <=50K.": "Less50K",
                                 " >50K": "More50K",
                                 " >50K.": "More50K"
                                 })
Adults["Income"].value_counts()

Less50K    37155
More50K    11687
Name: Income, dtype: int64

Now that we have a proper response variable, it is evident that $76$% of the people in the census make less than $\$50,000$. This can lead to faulty conclusions about the accuracy of the model in the later stages of this project.

## Feature Engineering:

This part involves creating new variables based on the existing ones.

Here is a list of the features that we will be creating:

1. Seniority - binary:
   
   * An indicator for whether a person is over the age of $50$ or not.

2. Overtime - binary:

    * An indicator for whether a person has worked overtime or not.

3. NetCapitalGain - continuous:

    * The net capital gain of a person.

4. GovWorker - binary:

    * An indicator for whether a person is a government worker or not.

5. Marital - categorial:
   
   * A nominal variable describing a person's marital status.

In [9]:
# 1. Create a variable based on seniority of the person's age
Adults["Seniority"] = np.where(Adults["Age"] >= 50, "Senior", "Youth")

# 2. Do they work overtime?
Adults["Overtime"] = np.where(Adults["Hours_Week"] > 40, "Yes", "No")

# 3. Net Capital Gain
Adults["NetCapitalGain"] = (Adults["Capital_Gain"] - Adults["Capital_Loss"])

# 4. Government worker or private sector
gov_dict = {" Private": "No", " Self-emp-not-inc": "No",
            " Local-gov": "Yes", " ?": "?", " State-gov": "Yes",
            " Self-emp-inc": "No", " Federal-gov": "Yes",
            " Without-pay": "No", " Never-worked": "No"}

Adults["GovWorker"] = Adults["WorkClass"].map(gov_dict)

marital_dict = {" Never-married": "Never-married",
                " Married-civ-spouse": "Married",
                " Divorced": "Divorced",
                " Separated": "Separated",
                " Widowed": "Widowed",
                " Married-spouse-absent": "Married",
                " Married-AF-spouse": "Married"}

Adults["Marital"] = Adults["Marital"].map(marital_dict)

Since our feature engineering is complete, let's drop the variables that don't provide additional information to our models.

In [10]:
drop_cols = ["Education", "Capital_Gain", "Capital_Loss", "WorkClass"]
Adults.drop(drop_cols, axis=1, inplace=True)

In [11]:
IncomeByMarital = Adults.groupby(["Marital", "Income"]).size()
IncomeByMarital = IncomeByMarital.reset_index()
IncomeByMarital.columns = ["Marital", "Income", "Count"]
IncomeByMarital

Marital   Income  Count
0       Divorced  Less50K   5962
1       Divorced  More50K    671
2        Married  Less50K  12988
3        Married  More50K  10056
4  Never-married  Less50K  15384
5  Never-married  More50K    733
6      Separated  Less50K   1431
7      Separated  More50K     99
8        Widowed  Less50K   1390
9        Widowed  More50K    128

In [12]:
fig = px.bar(IncomeByMarital, x="Marital", y="Count", color="Income",
             title="Count of Income by Marital Status", barmode="group")
fig.show()

Clearly, if you are married, you're chances of making $50,000 or more are higher than if you're not married.

Those who are single probably lean towards the younger side and thus are not as advanced in his/her careers.

### Combining Categories:

This step involves combining levels of a factor into a more meaningful format.

In [13]:
# 8. Combine some levels in order to reduce the number of levels for each categorical variable
def CombineCategories(df, Category: str, N: int):
    top_N = df[Category].value_counts().nlargest(N).index
    update = df[Category].where(df[Category].isin(top_N), other="Other")
    return update

country = CombineCategories(Adults, "NativeCountry", N=2)
Adults["NativeCountry"] = country
Adults["NativeCountry"].value_counts()

 United-States    43832
Other              4059
 Mexico             951
Name: NativeCountry, dtype: int64

Combining the levels of the Occupation variable:

In [14]:
occupation = CombineCategories(Adults, "Occupation", N=7)
Adults["Occupation"] = occupation
Adults["Occupation"].value_counts()

Other                 11412
 Prof-specialty        6172
 Craft-repair          6112
 Exec-managerial       6086
 Adm-clerical          5611
 Sales                 5504
 Other-service         4923
 Machine-op-inspct     3022
Name: Occupation, dtype: int64

This step is purely for aesthetic purposes. Rearrange the variables.

In [15]:
# 8. Reorder the columns:
columns = ["Age", "FnlWGT", "Education_Num", "Marital", "Occupation",
           "Relationship", "Race", "Sex", "Hours_Week", "NativeCountry",
           "Seniority", "Overtime", "NetCapitalGain", "GovWorker", "Income"]
Adults = Adults[columns]
Adults.head(4)

Age  FnlWGT  Education_Num        Marital        Occupation  ... Seniority  \
0   39   77516             13  Never-married      Adm-clerical  ...     Youth   
1   50   83311             13        Married   Exec-managerial  ...    Senior   
2   38  215646              9       Divorced             Other  ...     Youth   
3   53  234721              7        Married             Other  ...    Senior   

  Overtime NetCapitalGain  GovWorker   Income  
0       No           2174        Yes  Less50K  
1       No              0         No  Less50K  
2       No              0         No  Less50K  
3       No              0         No  Less50K  

[4 rows x 15 columns]

## Pre-procssing:

This part will involve the following steps:

1. Remove duplicate rows, if any.

2. Remove duplicate variables, if any.

3. Remove rows with a `"high"` % of missing values.

4. Remove variables that have non-unique values.

5. Drop zero-variance variables.

6. One-hot encoding / dummy variables.

7. Scaling continuous variables.

In [16]:
from sklearn.feature_selection import VarianceThreshold
from sklearn.preprocessing import LabelEncoder, OrdinalEncoder
from sklearn import preprocessing

In [17]:
Continuous = list(Adults.select_dtypes(include=['int64', 'float64']).columns)

def duplicate(df):
    start = df.shape[0]
    df2 = df.drop_duplicates(keep="first")
    end = df2.shape[0]
    print(f"Dropped {start - end} duplicates")
    return df2


df = duplicate(Adults)


Dropped 63 duplicates


2. Dropping duplicate variables.

In [18]:
def duplicate_vars(df):
    """Returns all of the duplicate variables by name
       Then you would delete them using a dictionary"""
    variables = list(df.columns)
    predictors = [var for var in variables if variables.count(var) >= 2]
    return set(predictors)

duplicate_vars(df) # Should be an empty set for this project.

set()

3. Removing rows with a `"high"` % of missing values.

In [19]:
# To see what % of the data is missing for each variable
missing_values = df.isnull().sum() / len(df) * 100
missing_values[missing_values > 0].sort_values(ascending=False)
missing_values


"TO REMOVE VARIABLES WITH HIGH % OF MISSING VALUES:"
# This is a custom function I made based on someone else's work
# Source: https://www.kaggle.com/pavansanagapati/simple-tutorial-dimensionality-reduction-methods


def high_missing_filter(df, missingPercent):
    variables = df.columns
    variable = []
    for i in range(0, len(df.columns)):
        if missing_values[i] <= missingPercent:
            variable.append(variables[i])
    # Keep only rows with missing % under threshold
    result = df.filter(items=variable)
    return result

df = high_missing_filter(df, missingPercent=50)
np.shape(df)

(48779, 15)

4. Remove variables that have non-unique values.

In [20]:
"To check for variables that have non-unique values:"
def nonunique_columns(df: pd.DataFrame):
    for col in df.columns:
        if len(df[col].unique()) == 1:
            return col


nonunique_columns(df)  # Noice

5. Drop zero-variance variables.

In [21]:
def LowVariance(df, Continuous, Threshold):
    dfCont = df[Continuous]  # Select just the continuous data
    selector = VarianceThreshold(threshold=Threshold)
    selector.fit(dfCont)
    constant_columns = [column for column in dfCont.columns
                        if column not in dfCont.columns[selector.get_support()]]
    return constant_columns  # Which variables are constant?


# Show the low-variance variables:
LowVariance(df, Continuous, Threshold=0.0)

[]

Re-create the Categorical and Continuous variables list.

In [22]:
Continuous = list(df.select_dtypes(include=['int64', 'float64']).columns)
Categorical = list(df.select_dtypes(include=['object', 'category']).columns)
Categorical.remove("Income")

6. One-hot encoding / dummy variables.

In [23]:
Nominal = list(df.select_dtypes(include=['object', 'category']).columns)
# Remove the ordinal and response variables, one by one
Nominal.remove("Income")
Nominal.remove("Seniority")
# One-hot encode the nominal variables
df = pd.get_dummies(df, drop_first=True, columns=Nominal)
df.head(4)

Age  FnlWGT  Education_Num  Hours_Week Seniority  ...  \
0   39   77516             13          40     Youth  ...   
1   50   83311             13          13    Senior  ...   
2   38  215646              9          40     Youth  ...   
3   53  234721              7          40    Senior  ...   

   NativeCountry_ United-States NativeCountry_Other  Overtime_Yes  \
0                             1                   0             0   
1                             1                   0             0   
2                             1                   0             0   
3                             1                   0             0   

   GovWorker_No  GovWorker_Yes  
0             0              1  
1             1              0  
2             1              0  
3             1              0  

[4 rows x 33 columns]

Ordinal Label Encoding:

In [24]:
def OrdinalEncode(data, OrdinalColumns: list):
    # You have to make a list of your ordinal variables first
    OE = OrdinalEncoder()
    for feature in OrdinalColumns:
        try:
            data[feature] = OE.fit_transform(data[[feature]])
        except:
            print(f"Error encoding {feature}")
    return data


# This is where you make a list of your ordinal features.
Ordinal = ["Seniority"]
df = OrdinalEncode(data=df, OrdinalColumns=Ordinal)
df.head(4)

Age  FnlWGT  Education_Num  Hours_Week  Seniority  ...  \
0   39   77516             13          40        1.0  ...   
1   50   83311             13          13        0.0  ...   
2   38  215646              9          40        1.0  ...   
3   53  234721              7          40        0.0  ...   

   NativeCountry_ United-States NativeCountry_Other  Overtime_Yes  \
0                             1                   0             0   
1                             1                   0             0   
2                             1                   0             0   
3                             1                   0             0   

   GovWorker_No  GovWorker_Yes  
0             0              1  
1             1              0  
2             1              0  
3             1              0  

[4 rows x 33 columns]

7. Scaling Continuous Variables.

In [25]:
scaler = preprocessing.RobustScaler()  # Define the scaling method
"If your data is skewed, use the Robust Scaler"
"If your features are normally distributed, use the Standard Scaler"
"Use MinMax as default, if no outliers"
df[Continuous] = scaler.fit_transform(df[Continuous]) 

In [26]:
# For some reason, the NetCapitalGain variable won't behave properly and scale down, so I scaled it myself using a Z-score
df["NetCapitalGain"] = (df["NetCapitalGain"] -
                        np.mean(df["NetCapitalGain"])) / np.std(df["NetCapitalGain"])
df["NetCapitalGain"].describe()

count    4.877900e+04
mean    -1.179369e-16
std      1.000010e+00
min     -7.150659e-01
25%     -1.327296e-01
50%     -1.327296e-01
75%     -1.327296e-01
max      1.323574e+01
Name: NetCapitalGain, dtype: float64

In [27]:
fig = px.histogram(df[Continuous])
fig.show()

### Train-Test Split:

In [28]:
from sklearn.model_selection import train_test_split, GridSearchCV

In [29]:
###############################################################################
###                     6. Train-Test Split                                 ###
###############################################################################

"Train-Test Split"

# Define X and Y variables

# Replace Class with your response variable
y = df["Income"]
x = df.drop(["Income"], axis=1)  # Drop any unneeded variables

x_train, x_test, y_train, y_test = train_test_split(
    x, y,
    test_size=0.25,  # 75/25
    random_state=123,
    stratify=y,  # For classification only
    shuffle=True)

### Hyperparameter Tuning:

The hyperparameters must be in square brackets.

In [30]:
import sklearn
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier

In [31]:

# Add models as you wish
Models = {
    "Logistic Regression": LogisticRegression(),
    "Random Forest": RandomForestClassifier(),
    "Ada Boost": AdaBoostClassifier(),
    "SVClassifier": SVC(),
    "KNN": KNeighborsClassifier(),
    "LDA": LinearDiscriminantAnalysis()
}

HyperParams = {}  # Start with an empty dictionary

help(sklearn.linear_model.LogisticRegression())

HyperParams.update({"Logistic Regression":
                    {"max_iter": [200],
                     "verbose": [1],
                     "n_jobs": [-1]
                     }})

HyperParams.update({"Random Forest": {
    "n_estimators": [350],
    "class_weight": ["balanced"],
    "max_features": ["auto", "sqrt", "log2"],
    "max_depth": [3, 4, 5, 6, 7, 8],
    "min_samples_split": [0.005, 0.01, 0.05],
    "min_samples_leaf": [0.005, 0.01, 0.05, 0.10],
    "n_jobs": [-1]
}})

help(sklearn.ensemble.AdaBoostClassifier())

HyperParams.update({"Ada Boost":
                    {"n_estimators": [400],
                     "learning_rate": [0.001, 0.05, 0.10, 0.5]
                     }})

help(sklearn.svm.SVC())
HyperParams.update({"SVClassifier":
                    {"kernel": ["rbf"],
                     "verbose": [True],
                     "gamma": [0.001, 0.0001]
                     }})

help(sklearn.neighbors.KNeighborsClassifier)
HyperParams.update({"KNN":
                    {"n_neighbors": [3],
                     "algorithm": ["auto"],
                     "n_jobs": [-1]
                     }})

help(sklearn.discriminant_analysis.LinearDiscriminantAnalysis)
HyperParams.update({"LDA":
                    {"solver": ["eigen"],
                     "store_covariance": [False],
                     "shrinkage": [None]
                     }})

Help on LogisticRegression in module sklearn.linear_model._logistic object:

class LogisticRegression(sklearn.linear_model._base.LinearClassifierMixin, sklearn.linear_model._base.SparseCoefMixin, sklearn.base.BaseEstimator)
 |  LogisticRegression(penalty='l2', *, dual=False, tol=0.0001, C=1.0, fit_intercept=True, intercept_scaling=1, class_weight=None, random_state=None, solver='lbfgs', max_iter=100, multi_class='auto', verbose=0, warm_start=False, n_jobs=None, l1_ratio=None)
 |  
 |  Logistic Regression (aka logit, MaxEnt) classifier.
 |  
 |  In the multiclass case, the training algorithm uses the one-vs-rest (OvR)
 |  scheme if the 'multi_class' option is set to 'ovr', and uses the
 |  cross-entropy loss if the 'multi_class' option is set to 'multinomial'.
 |  (Currently the 'multinomial' option is supported only by the 'lbfgs',
 |  'sag', 'saga' and 'newton-cg' solvers.)
 |  
 |  This class implements regularized logistic regression using the
 |  'liblinear' library, 'newton-cg', '

### Running Our Models:

[Major Source:](http://www.davidsbatista.net/blog/2018/02/23/model_optimization/)

This is where the magic happens.

In [32]:
class EstimatorSelectionHelper:

    def __init__(self, models, params):
        if not set(models.keys()).issubset(set(params.keys())):
            missing_params = list(set(models.keys()) - set(params.keys()))
            raise ValueError(
                "Some estimators are missing parameters: %s" % missing_params)
        self.models = models
        self.params = params
        self.keys = models.keys()
        self.grid_searches = {}

    def fit(self, X, y, cv=3, n_jobs=-1, verbose=1, scoring=None, refit=False):
        for key in self.keys:
            print(f"Running GridSearchCV for {key}.")
            model = self.models[key]
            params = self.params[key]
            gs = GridSearchCV(model, params, cv=cv, n_jobs=n_jobs,
                              verbose=verbose, scoring="accuracy", refit=refit,
                              return_train_score=True)
            gs.fit(X, y)
            self.grid_searches[key] = gs

    def score_summary(self, sort_by='mean_score'):
        def row(key, scores, params):
            d = {
                'estimator': key,
                'min_score': min(scores),
                'max_score': max(scores),
                'mean_score': np.mean(scores),
                'std_score': np.std(scores),
                "range_score": (max(scores) - min(scores))  # My own metric
            }
            return pd.Series({**params, **d})

        rows = []
        for k in self.grid_searches:
            print(k)
            params = self.grid_searches[k].cv_results_['params']
            scores = []
            for i in range(self.grid_searches[k].cv):
                key = "split{}_test_score".format(i)
                r = self.grid_searches[k].cv_results_[key]
                scores.append(r.reshape(len(params), 1))

            all_scores = np.hstack(scores)
            for p, s in zip(params, all_scores):
                rows.append((row(k, s, p)))

        df = pd.concat(rows, axis=1).T.sort_values([sort_by], ascending=False)

        columns = ['estimator', 'min_score', 'mean_score',
                   'max_score', 'std_score', "range_score"]
        columns = columns + [c for c in df.columns if c not in columns]

        return df[columns]

For the fitting procedure, simply pass in a dictionary of models and a dictionary of hyperparameters for those models.

In [33]:
pipeline = EstimatorSelectionHelper(Models, HyperParams)
pipeline.fit(x_train, y_train,
             cv=2, n_jobs=-2, refit=False,  # Change cv to whatever you want
             scoring="f1", verbose=2)
results = pipeline.score_summary(sort_by='mean_score')

Running GridSearchCV for Logistic Regression.
Fitting 2 folds for each of 1 candidates, totalling 2 fits
Running GridSearchCV for Random Forest.
Fitting 2 folds for each of 216 candidates, totalling 432 fits
Running GridSearchCV for Ada Boost.
Fitting 2 folds for each of 4 candidates, totalling 8 fits
Running GridSearchCV for SVClassifier.
Fitting 2 folds for each of 2 candidates, totalling 4 fits
Running GridSearchCV for KNN.
Fitting 2 folds for each of 1 candidates, totalling 2 fits
Running GridSearchCV for LDA.
Fitting 2 folds for each of 1 candidates, totalling 2 fits
Logistic Regression
Random Forest
Ada Boost
SVClassifier
KNN
LDA


In [53]:
print(results)

               estimator min_score  mean_score max_score std_score  ...  \
220            Ada Boost  0.863547    0.863984  0.864422  0.000437  ...   
219            Ada Boost  0.856713    0.857342  0.857971  0.000629  ...   
218            Ada Boost  0.854417    0.855073  0.855729  0.000656  ...   
0    Logistic Regression  0.839711    0.841925   0.84414  0.002214  ...   
221         SVClassifier  0.835775    0.836568  0.837361  0.000793  ...   
..                   ...       ...         ...       ...       ...  ...   
118        Random Forest  0.714848    0.719878  0.724907   0.00503  ...   
10         Random Forest  0.716652    0.719850  0.723048  0.003198  ...   
178        Random Forest  0.715395    0.719249  0.723103  0.003854  ...   
22         Random Forest  0.713099    0.718812  0.724524  0.005713  ...   
36         Random Forest  0.715176    0.717253  0.719331  0.002077  ...   

    algorithm n_neighbors shrinkage solver store_covariance  
220       NaN         NaN       NaN  

In [47]:
results["mean_score"] = results["mean_score"].astype(float)

Choosing the **best** model.

In [54]:
results.loc[results['mean_score'].idxmax()]

estimator            Ada Boost
min_score             0.863547
mean_score            0.863984
max_score             0.864422
std_score             0.000437
range_score           0.000875
max_iter                   NaN
n_jobs                     NaN
verbose                    NaN
class_weight               NaN
max_depth                  NaN
max_features               NaN
min_samples_leaf           NaN
min_samples_split          NaN
n_estimators               400
learning_rate              0.5
gamma                      NaN
kernel                     NaN
algorithm                  NaN
n_neighbors                NaN
shrinkage                  NaN
solver                     NaN
store_covariance           NaN
Name: 220, dtype: object

## Trying out XGBoost:

In [31]:
from xgboost import XGBClassifier
from sklearn.model_selection import cross_val_score

In [32]:
cross_val_score(XGBClassifier(), x_train, y_train, cv=5, n_jobs=-1)

array([0.87030204, 0.86538199, 0.86114528, 0.87221539, 0.86550027])

That took about 4 seconds. Wow.